# 📊 **Re-Implementation of "Predicting Food Crises Using News Streams"**

---

#### 🔍 **Objective**

This notebook aims to **reproduce and analyze** the methodology presented in the paper:

📄 **Paper:** [Predicting food crises using news streams](https://www.science.org/doi/10.1126/sciadv.abm3449)  
📊 **Dataset:** [Harvard Dataverse Repository](https://dataverse.harvard.edu/dataset.xhtml?persistentId=doi:10.7910/DVN/CJDWUW)  
📜 **Original Code & Methods:** [GitHub - Regression Modeling (Step 5)](https://github.com/philippzi98/food_insecurity_predictions_nlp/blob/main/Step%205%20-%20Regression%20Modelling/README.md)

---

#### 🛠 **Methodology**

This implementation follows the **key steps** outlined in the paper to predict **food insecurity crises** using a combination of:
1️⃣ **Traditional Risk Factors** (conflict, climate, food prices, etc.)  
2️⃣ **News-Based Indicators** (text feature frequencies from news articles)  
3️⃣ **Lagging & Aggregation** (temporal dependencies at district, province, and country levels)  
4️⃣ **Machine Learning Models** (Random Forest, OLS, Lasso)

---

#### 🔗 **Reference Materials**

📄 **Supplementary Material:** Available in `supplemental_material_from_paper.pdf`  
📊 **Datasets Used:**

- `time_series_with_causes_zscore_full.csv` (Main dataset with time-series features)
- `famine-country-province-district-years-CS.csv` (Food insecurity classification)
- `matching_districts.csv` (Geographical standardization)


# 📚🔧 Import Libraries

In this notebook, we will use uv to manage our Python environment and packages efficiently. uv is a modern and fast package manager that simplifies virtual environment creation, and dependency installation. We will create a virtual environment, install necessary libraries, and ensure our environment stays consistent across different setups.


In [49]:
## Uncoment the below cell to install `uv` if you have not already. You can also install it trhiugh `pip` by running `!pip install uv` but this will be within your current python environment and not globally.

# !curl -LsSf https://astral.sh/uv/install.sh | sh
# !uv venv world-bank
# !source world-bank/bin/activate

In [50]:
# !uv pip install -r requirements.txt

In [51]:
import pandas as pd
import numpy as np
import folium
from IPython.display import display, Image
import os
import gdown
import zipfile
import editdistance
from fuzzywuzzy import fuzz
import math

In [52]:
url = "https://drive.google.com/uc?id=1YoQ1hz9RlaLr2xW3KoKCfJPyyO2PErym"
output = "data.zip"

if not os.path.exists("./data"):
    gdown.download(url, output, quiet=False) 
    zipfile.ZipFile('data.zip', 'r').extractall()
else:
    print("You already have the data downloaded and extracted")

You already have the data downloaded and extracted


## 📂 Load and Clean Data

**Understanding the Time-Series Dataset & Column Selection**

This dataset contains **district-level time-series data** on food insecurity risk factors, including:

- **📅 Temporal Information:** `year`, `month`, `year_month`
- **📍 Geographical Identifiers:** `admin_code`, `admin_name`, `province`, `country`
- **🌍 Traditional Risk Factors:** Climate (`rain_mean`, `ndvi_mean`), conflict (`acled_count`), food prices (`p_staple_food`)
- **📰 News-Based Indicators:** Proportions of news articles mentioning crisis-related keywords (`conflict_0`, `famine_0`, etc.)
- **📉 Food Insecurity Label:** `fews_ipc` (Integrated Phase Classification)

🔥 **Columns We Will Drop & Why**
✔ **Redundant Aggregations:** `_1`, `_2` columns (province & country-level values) since we will recompute aggregations from scratch anyways.  
✔ **Unnamed/Index Columns:** `Unnamed: 0` as it is unnecessary. It is just a duplicate of default index.
✔ **Unnecessary Identifiers:** If `admin_code` and `admin_name`, after matching these to `matching_districts.csv`, we can drop them.

---

> ⚠️ **NOTE:**  
> For a detailed explanation of the dataset and features, refer to the [`explore_time_series.ipynb`](./explore_time_series.ipynb) notebook.


In [53]:
time_series = pd.read_csv('./data/time_series_with_causes_zscore_full.csv')
admins = pd.read_csv('./data/famine-country-province-district-years-CS.csv')
valid_matching = pd.read_csv('./data/matching_districts.csv')

In [54]:
sorted(time_series.columns.values)

['Unnamed: 0',
 'abnormally low rainfall_0',
 'abnormally low rainfall_1',
 'abnormally low rainfall_2',
 'acled_count',
 'acled_fatalities',
 'acute hunger_0',
 'acute hunger_1',
 'acute hunger_2',
 'admin_code',
 'admin_name',
 'aid appeal_0',
 'aid appeal_1',
 'aid appeal_2',
 'aid workers died_0',
 'aid workers died_1',
 'aid workers died_2',
 'air attack_0',
 'air attack_1',
 'air attack_2',
 'alarming level_0',
 'alarming level_1',
 'alarming level_2',
 'anti-western policies_0',
 'anti-western policies_1',
 'anti-western policies_2',
 'apathy_0',
 'apathy_1',
 'apathy_2',
 'area',
 'asylum seekers_0',
 'asylum seekers_1',
 'asylum seekers_2',
 'authoritarian_0',
 'authoritarian_1',
 'authoritarian_2',
 'bad harvests_0',
 'bad harvests_1',
 'bad harvests_2',
 'blockade_0',
 'blockade_1',
 'blockade_2',
 'bombing campaign_0',
 'bombing campaign_1',
 'bombing campaign_2',
 'brain drain_0',
 'brain drain_1',
 'brain drain_2',
 'brutal government_0',
 'brutal government_1',
 'brutal 

In [55]:
time_series.head(5)

Unnamed: 0  index      country  admin_code admin_name      centx  \
0           0     30  Afghanistan         202   Kandahar  65.709343   
1           1     33  Afghanistan         202   Kandahar  65.709343   
2           2     36  Afghanistan         202   Kandahar  65.709343   
3           3     39  Afghanistan         202   Kandahar  65.709343   
4           4     42  Afghanistan         202   Kandahar  65.709343   

       centy year_month  year  month  ...  carbon_2  mayhem_0  mayhem_1  \
0  31.043618    2009_07  2009      7  ...  1.053000  0.667000 -0.171000   
1  31.043618    2009_10  2009     10  ... -0.660812 -0.636580 -0.520247   
2  31.043618    2010_01  2010      1  ... -0.134333  1.447667 -0.844333   
3  31.043618    2010_04  2010      4  ... -0.326927 -0.594877  0.164790   
4  31.043618    2010_07  2010      7  ... -1.085146 -0.709913 -0.867913   

   mayhem_2  dehydrated_0  dehydrated_1  dehydrated_2  mismanagement_0  \
0 -0.833000      0.173667      0.168000      1.284667        -0.073000   
1 -0.782913     -0.671587     -0.612254     -0.926921        -0.510467   
2  0.778667     -0.676000     -0.689667      0.293333         0.530333   
3 -0.905210     -0.620540      0.165794      0.045794        -1.011600   
4 -0.770247     -0.787921     -0.974587     -0.946921        -0.611133   

   mismanagement_1  mismanagement_2  
0        -0.427667         0.668333  
1        -0.625133        -0.452467  
2        -0.471333         0.955333  
3        -0.810600        -0.205600  
4        -0.709800        -0.622800  

[5 rows x 532 columns]

In [56]:
t_variant_traditional_factors = ['ndvi_mean', 'ndvi_anom', 'rain_mean', 'rain_anom', 'et_mean', 'et_anom', 
                                    'acled_count', 'acled_fatalities', 'p_staple_food']
t_invariant_traditional_factors = ['area', 'cropland_pct', 'pop', 'ruggedness_mean', 'pasture_pct']
news_factors = [name for name in time_series.columns.values if '_0' in name]

In [57]:
news_factors[0]

'land seizures_0'

In [58]:
print("Columns count BEFORE dropping: ", len(time_series.columns.values))

Columns count BEFORE dropping:  532


In [59]:
cols_to_drop = ["Unnamed: 0", "centx", "centy", 'change_fews', 'fews_ha', 'fews_proj_med', 'fews_proj_med_ha', 'fews_proj_near_ha'] + [col for col in time_series.columns if col.endswith(('_1', '_2', '_3'))]
time_series.drop(columns=cols_to_drop, inplace=True)

In [60]:
potential_extra_cols = set(time_series.columns.values) - set(t_variant_traditional_factors) - set(t_invariant_traditional_factors) - set(news_factors)
potential_extra_cols = [col for col in potential_extra_cols if not col.endswith(('_1', '_2', '_3'))]
print("Potential extra columns", potential_extra_cols)

Potential extra columns ['index', 'month', 'year', 'admin_code', 'fews_proj_near', 'country', 'admin_name', 'year_month', 'fews_ipc']


In [61]:
print("Columns count after dropping: ", len(time_series.columns.values))

Columns count after dropping:  190


In [62]:
# time_series = time_series.iloc[:5]
# print("Row count after keeping first 5 rows:", len(time_series))

### 🌍 Admin Level Mapping: Standardizing Geographical Identifiers

In this section, we will **map and standardize** the `admin_code` and `admin_name` fields to their corresponding **district, province, and country names**. This step is **crucial** for ensuring **consistency** across different datasets and enabling **accurate aggregations** at multiple administrative levels.

🛠 **Why is Admin Level Mapping Important?**
✅ Different datasets may use **slightly different spellings or formats** for district names.  
✅ Some district names might be **missing or misspelled**, requiring standardization.  
✅ We need to **match and align** district names across various sources before aggregating at **province and country levels**.  
✅ Proper mapping allows us to **merge datasets correctly** without losing information.  

📌 **Steps in Admin Mapping**
1️⃣ **Load the `matching_districts.csv` file**, which provides the mapping between different district name variations.  
2️⃣ **Identify missing or unmatched `admin_name` values** and find their closest matches using fuzzy matching techniques.  
3️⃣ **Ensure that each `admin_code` uniquely maps to one `district`, `province`, and `country`.**  
4️⃣ **Replace inconsistent names** in the dataset with their standardized versions.  
5️⃣ **Aggregate data at the `province` and `country` levels** after ensuring all districts are correctly mapped.  


In [63]:
len(admins.country.unique())

39

In [64]:
admins.columns.values

array(['Unnamed: 0', 'country', 'district', 'year', 'month', 'CS',
       'province'], dtype=object)

In [65]:
admin_names = time_series['admin_name'].unique()
districts = admins['district'].unique()
provinces = admins['province'].unique()
countries = admins['country'].unique()

In [66]:
print (len(admin_names), len(districts), len(provinces), len(countries))
print (len(set(admin_names).difference(districts)))
missing_admin_names = set(admin_names).difference(districts)
print (len(missing_admin_names.difference(provinces)))
missing_admin_names = missing_admin_names.difference(provinces)

1142 4113 474 39
369
230


### Fuzzy String Matching for Missing Names

The function uses **fuzzy string matching** to find the best approximate matches for missing administrative names (e.g., districts and provinces). 

- Finds the **best matching district/province** for each missing name.
- Uses **fuzzy string matching** to calculate the similarity between missing names and known names.
- Returns a dictionary that maps each missing name to its closest match.


In [67]:
def find_matching(missing, names):
    matching_districts = {}
    for m in missing:
        max_overlap = 0
        nearest_d = None
        for d in names:
            d = str(d)
            dist = fuzz.partial_ratio(m, d)
            if dist > max_overlap:
                max_overlap = dist
                nearest_d = d
        matching_districts[m] = nearest_d
    return matching_districts


matching = find_matching(missing_admin_names, districts)
matching_p = find_matching(missing_admin_names, provinces)

# manually verify matching and update
for k in matching.keys():
    print (k, matching[k], matching_p[k])


Trans Mara Marka Mara
Gedio Gedeo Gedo
Kisangani City of Kisangani Tanga
Lac-Léré Lac-Lere Lac
Shar'ab As Salam Shar`ab As Salam Mara
Ceca La Source Cerca La Source Sud
Ghebeish Nesh Abyei
Grande Riviere Du Nord Grande Riviere du Nord Nord
North Shewa(R4) North Shewa North
Ad Dali' Ad Dali` Ad Dali`
Abu Hamad Abu Hamed Hilmand
Amran `Amran `Amran
Ad Douiem El Douiem Ad Dali`
Mbeere Mbeere North Mbeya
Sheikh Jebrat El Sheikh Sahel
Maïné Soroa Maine Soroa Sool
Gebiley Gabiley Blue Nile
Wadi Halfa Halfa Wadi Fira
North Gonder North Gondar North
Bukavu City of Bukavu Busia
Baw Bahr El Arab Western Bahr el Ghazal
KT Koch Haute-Kotto
Gucha Kabuchai Ahuachapan
Meru North Meru Meru
Abu Jubaiyah Juba Raymah
Al Kurumik Qulansiyah wa `Abd Al Kuri Ituri
Al Fushqa Al Husha' Arusha
Kindu City of Kindu Kunduz
Adan Aldai `Adan
South Khartoum Khartoum Khartoum
Chegutu Chegutu Rural Hodh ech Chargui
Port De Paix Port de Paix Pwani
Hamashkorieb Hamashkoreib Ghor
Bindura Bindura Urban Cabinda
Eastern Tigr

### Encoding Decoding

`to_ascii_escaped(s)`: Converts a Unicode string to an ASCII-safe representation using **unicode-escape**.

`from_ascii_escaped(escaped)`: Converts the escaped ASCII string back into its original Unicode form.

In [68]:
def to_ascii_escaped(s):
    """
    Convert a Unicode string to an ASCII-safe string using unicode-escape.
    This will replace non-ASCII characters with their escape sequences.
    """
    if isinstance(s, bytes):
        s = s.decode('utf-8')
    # Using 'unicode-escape' encoding produces a bytes object,
    # then decode it to get an ASCII string.
    return s.encode('unicode-escape').decode('ascii')

def from_ascii_escaped(escaped):
    """
    Convert the ASCII-escaped string back to the original Unicode string.
    """
    # Encode the ASCII string to bytes, then decode using 'unicode-escape'
    return escaped.encode('ascii').decode('unicode-escape')


### Finding the Province for a Given District or Province

`find_province(x)`, finds the **province** corresponding to a given administrative name. It accounts for:
- **Direct Lookups** (Exact match in known district/province lists)
- **Fuzzy Matching** (Using ASCII-safe transformation for inconsistent text encoding)
- **Validation Against a Predefined Mapping (`valid_matching`)**

In [69]:
# Define matched globally
matched = valid_matching['missing'].unique()

def to_ascii_escaped(s):
    """
    Convert a Unicode string to an ASCII-safe string using unicode-escape.
    This will replace non-ASCII characters with their escape sequences.
    """
    if isinstance(s, bytes):
        s = s.decode('utf-8')
    return s.encode('unicode-escape').decode('ascii')

def find_province(x):
    try:
        # Ensure x is a Unicode string.
        if isinstance(x, bytes):
            x = x.decode('utf-8')
        
        # Direct lookup in districts or provinces.
        if x in districts:
            return admins[admins['district'] == x]['province'].values[0]
        elif x in provinces:
            return x

        # Convert x to an ASCII-escaped version.
        escaped_x = to_ascii_escaped(x)
        
        # Check if the escaped version is in matched.
        if escaped_x in matched:
            v = valid_matching[valid_matching['missing'] == escaped_x]
            if v['match'].values[0] == 'district':
                x2 = v['district'].values[0]
                return admins[admins['district'] == x2]['province'].values[0]
            elif v['match'].values[0] == 'province':
                return v['province'].values[0]
        
        # If no conditions are met, raise an exception.
        raise Exception("No matching province found")
    except Exception as e:
        raise Exception("Province not found for: {} ({})".format(x, e))


### Handling Admin Names with Accented Characters and Mapping to Provinces

Maps `admin_names` to provinces using the `find_province(a)` function.  
If a **direct lookup fails**, it tries to handle cases where the **admin name contains accented characters** (`é`, `è`, `ô`) ->  (encoding decoding issues resolved through directly replacing these with 'e' or 'o', leads to finding a valid match). 

In [70]:
admin_to_province = {}
for a in admin_names:
    try:
        admin_to_province[a] = find_province(a)
    except Exception as e:
        # Print the admin name that caused an error
        print("Error with:", a)
        # Check if a contains accented characters "é" or "è"
        if 'é' in a or 'è' in a or 'ô' in a:
            a_modified = a.replace('é', 'e').replace('è', 'e').replace('ô', 'o')
            # Check if the modified name is in districts
            if a_modified in districts:
                # Use the modified name to look up the province from admins
                try:
                    province = admins[admins['district'] == a_modified]['province'].values[0]
                    admin_to_province[a] = province
                    print(f"Replaced '{a}' with '{a_modified}', found province: {province}")
                except Exception as ex:
                    print(f"Modified name '{a_modified}' not found in admins: {ex}")
            else:
                print(f"Modified name '{a_modified}' not in districts.")
        else:
            print(f"No accented e found in '{a}'.")


Error with: Mangalmé
Replaced 'Mangalmé' with 'Mangalme', found province: Guera
Error with: La Pendé
Replaced 'La Pendé' with 'La Pende', found province: Logone Oriental
Error with: La Nya Pendé
Replaced 'La Nya Pendé' with 'La Nya Pende', found province: Logone Oriental
Error with: Lac-Léré
Replaced 'Lac-Léré' with 'Lac-Lere', found province: Mayo-Kebbi Ouest
Error with: Barh-Kôh
Replaced 'Barh-Kôh' with 'Barh-Koh', found province: Moyen-Chari
Error with: Aguié
Replaced 'Aguié' with 'Aguie', found province: Maradi
Error with: Bankilaré
Replaced 'Bankilaré' with 'Bankilare', found province: Tillaberi
Error with: Filingué
Replaced 'Filingué' with 'Filingue', found province: Tillaberi
Error with: Gothèye
Replaced 'Gothèye' with 'Gotheye', found province: Tillaberi
Error with: Gouré
Replaced 'Gouré' with 'Goure', found province: Zinder
Error with: Illéla
Replaced 'Illéla' with 'Illela', found province: Sokoto
Error with: Kantché
Replaced 'Kantché' with 'Kantche', found province: Zinder
Er

### Mapping Administrative Names to Provinces in time_series

Maps `admin_name` to their respective **provinces** using a precomputed dictionary - >`admin_to_province` in `time_series`.


In [71]:
time_series['province'] = time_series['admin_name'].apply(
    lambda x: admin_to_province[x] if x in admin_to_province else admin_to_province.get(x.replace('ô', 'o'))
)


In [72]:
time_series[["admin_name", "province"]]

admin_name  province
0        Kandahar  Kandahar
1        Kandahar  Kandahar
2        Kandahar  Kandahar
3        Kandahar  Kandahar
4        Kandahar  Kandahar
...           ...       ...
40947  Zvishavane  Midlands
40948  Zvishavane  Midlands
40949  Zvishavane  Midlands
40950  Zvishavane  Midlands
40951  Zvishavane  Midlands

[40952 rows x 2 columns]

# ⏳ Time Lagging & Feature Engineering

#### 📅 **Why Use Lagging?**

To predict food insecurity **for a given quarter**, we use:

- **6 months of historical values** for traditional & news-based features.
- **Province & country-level aggregations** to capture broader shocks.
- **6 quarters of lagged IPC phase values** to model temporal dependencies.

#### ⚡ **Optimized Lagging Approach**

To improve computational efficiency, we:
✔ Use `groupby()` for **fast province & country-level aggregations**.  
✔ Merge lagged data via `merge()` instead of slow `.apply()`.  
✔ Only keep **past data** to ensure no data leakage.


In [73]:
# import pandas as pd

# def precompute_lagged_mapping():
#     """Precompute a dictionary for faster lookups of lagged values."""
#     time_series['year_month'] = time_series['year'].astype(str) + "_" + time_series['month'].astype(str)
#     return time_series.set_index(['admin_code', 'year_month']).to_dict(orient='index')

# def get_lagged(admin_code, year, month, f, t, lagged_map, default_value):
#     """Retrieve the lagged feature efficiently using precomputed mapping."""
#     l_month = ((month - 1 - t) % 12) + 1
#     l_year = year - 1 if month - t <= 0 else year
#     lagged_key = f"{l_year}_{l_month}"
    
#     return lagged_map.get((admin_code, lagged_key), {}).get(f, default_value)

# def add_time_lagged(features, start=3, end=9, diff=1, agg=True):
#     """Efficiently adds lagged features by using precomputed mappings."""
#     levels = ['', '_province', '_country'] if agg else ['']
#     lagged_map = precompute_lagged_mapping()
#     time_series['year_month'] = time_series['year'].astype(str) + "_" + time_series['month'].astype(str)
    
#     for suffix in levels:
#         for f in features:
#             f_s = f + suffix
#             for t in range(start, end, diff):
#                 lagged_col = f"{f_s}_{t}"
#                 if lagged_col in time_series.columns:
#                     continue
                
#                 time_series[lagged_col] = time_series.apply(
#                     lambda x: get_lagged(x['admin_code'], x['year'], x['month'], f_s, t, lagged_map, x[f_s]), axis=1
#                 )
#     return time_series

import pandas as pd
import numpy as np

def get_lagged(x, f, t, ts_dict):
    admin_code = x['admin_code']
    year, month = x['year'], x['month']

    # Compute lagged year and month
    l_month = ((month - 1 - t) % 12) + 1
    l_year = year - 1 if month - t <= 0 else year
    lagged_year_month = f"{l_year}_{l_month}"

    # Retrieve pre-filtered DataFrame
    ts = ts_dict.get(admin_code)

    # Ensure ts is a dictionary and extract only the requested feature
    if ts is not None and lagged_year_month in ts:
        lagged_values = ts[lagged_year_month]  # This might be a dictionary
        if isinstance(lagged_values, dict):
            return lagged_values.get(f, x[f])  # Extract only `f`
        return lagged_values  # Directly return value if not a dict

    return x[f]  # Fallback to original value


def add_time_lagged(features, start=3, end=9, diff=1, agg=True):
    levels = ['', '_province', '_country'] if agg else ['']

    # Convert 'year_month' to index and precompute admin_code groupings
    ts_dict = {ac: df.set_index('year_month')[features].to_dict(orient="index")
               for ac, df in time_series.groupby('admin_code')}

    for suffix in levels:
        for f in features:
            f_s = f + suffix
            for t in range(start, end, diff):
                lagged_col = f"{f_s}_{t}"

                if lagged_col in time_series.columns:
                    continue

                # Use list comprehension for better performance
                time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]

    return time_series  # Return modified DataFrame


# Province & Country-Level Aggregation

This function aggregates feature values at the province and country levels to capture regional trends, aiding in food insecurity prediction. The process includes:

- **Grouping by year_month and level:** Data is grouped by year_month and the specified level (province or country) to calculate the mean of features, reflecting regional trends over time.

- **Applying transformations efficiently:** Instead of merging aggregated data, `transform("mean")` is used to directly assign the computed mean to each row, avoiding unnecessary joins and improving performance.  

#### ⚡ **Efficiency Gains**

- **Fast Aggregation**: Uses `groupby()` for efficient aggregation.
- **Avoids Costly Joins**: Eliminates the need for `merge()` by using `transform()` instead, reducing computational overhead.  
- **Memory Efficiency**: Converts the `level` column to a categorical type to reduce memory usage.

This approach ensures faster processing while maintaining the quality of aggregated features.


In [74]:
def add_agg_factors(features, level='province'):
    global time_series  

    # Convert 'level' column to categorical for performance
    time_series[level] = time_series[level].astype('category')
    
    # Compute grouped mean values for the given features
    grouped_df = time_series.groupby(['year_month', level], observed=True, sort=False)[features].transform("mean")

    # Rename columns to include level
    grouped_df = grouped_df.rename(columns={f: f"{f}_{level}" for f in features})

    # Use pd.concat() to add all columns at once, avoiding fragmentation
    time_series = pd.concat([time_series, grouped_df], axis=1)

    return time_series


In [75]:
add_agg_factors(news_factors)

index      country  admin_code  admin_name year_month  year  month  \
0          30  Afghanistan         202    Kandahar    2009_07  2009      7   
1          33  Afghanistan         202    Kandahar    2009_10  2009     10   
2          36  Afghanistan         202    Kandahar    2010_01  2010      1   
3          39  Afghanistan         202    Kandahar    2010_04  2010      4   
4          42  Afghanistan         202    Kandahar    2010_07  2010      7   
...       ...          ...         ...         ...        ...   ...    ...   
40947  183579     Zimbabwe         612  Zvishavane    2018_10  2018     10   
40948  183583     Zimbabwe         612  Zvishavane    2019_02  2019      2   
40949  183587     Zimbabwe         612  Zvishavane    2019_06  2019      6   
40950  183591     Zimbabwe         612  Zvishavane    2019_10  2019     10   
40951  183595     Zimbabwe         612  Zvishavane    2020_02  2020      2   

       fews_ipc  fews_proj_near  ndvi_mean  ...  gastrointestinal_0_province  \
0           1.0             NaN   0.106035  ...                    -0.192000   
1           1.0             NaN   0.103009  ...                    -0.545727   
2           2.0             NaN   0.109600  ...                     1.506333   
3           2.0             NaN   0.111599  ...                    -0.793970   
4           1.0             NaN   0.096943  ...                    -0.509394   
...         ...             ...        ...  ...                          ...   
40947       3.0             3.0   0.326176  ...                     0.765375   
40948       3.0             3.0   0.497560  ...                     0.088125   
40949       3.0             3.0   0.377050  ...                     0.307691   
40950       3.0             3.0   0.297881  ...                    -0.231619   
40951       2.0             2.0   0.539183  ...                          NaN   

       terrorist_0_province  warlord_0_province  d'etat_0_province  \
0                 -0.284333           -0.668667           0.647333   
1                 -1.037016           -0.811291          -0.850261   
2                  0.455000            1.595667           0.571667   
3                 -0.722159           -0.130521           0.047630   
4                 -0.694350           -1.215958          -0.865261   
...                     ...                 ...                ...   
40947              0.391125            0.501417           0.571500   
40948             -0.147375            0.177167           0.108125   
40949             -0.300870            0.137749           0.275410   
40950              0.205385           -0.045085           0.077570   
40951                   NaN                 NaN                NaN   

       overthrow_0_province  convoys_0_province  carbon_0_province  \
0                 -0.891333            0.112667           1.265333   
1                 -0.948892           -0.728972          -0.765146   
2                  0.279000           -0.868333           0.058333   
3                  0.362613            0.480986           0.026073   
4                 -1.119225           -1.060638          -0.673479   
...                     ...                 ...                ...   
40947              0.012375            0.226250           0.183833   
40948              0.177833            0.363208           0.142167   
40949              0.281648            0.137628           0.333385   
40950              0.500754            0.199047          -0.009647   
40951                   NaN                 NaN                NaN   

       mayhem_0_province  dehydrated_0_province  mismanagement_0_province  
0               0.667000               0.173667                 -0.073000  
1              -0.636580              -0.671587                 -0.510467  
2               1.447667              -0.676000                  0.530333  
3              -0.594877              -0.620540                 -1.011600  
4              -0.709913              -0.787921 

In [76]:
add_agg_factors(news_factors, level='country')
time_series.head(10)

index      country  admin_code admin_name year_month  year  month  \
0     30  Afghanistan         202   Kandahar    2009_07  2009      7   
1     33  Afghanistan         202   Kandahar    2009_10  2009     10   
2     36  Afghanistan         202   Kandahar    2010_01  2010      1   
3     39  Afghanistan         202   Kandahar    2010_04  2010      4   
4     42  Afghanistan         202   Kandahar    2010_07  2010      7   
5     45  Afghanistan         202   Kandahar    2010_10  2010     10   
6     48  Afghanistan         202   Kandahar    2011_01  2011      1   
7     51  Afghanistan         202   Kandahar    2011_04  2011      4   
8     54  Afghanistan         202   Kandahar    2011_07  2011      7   
9     57  Afghanistan         202   Kandahar    2011_10  2011     10   

   fews_ipc  fews_proj_near  ndvi_mean  ...  gastrointestinal_0_country  \
0       1.0             NaN   0.106035  ...                    0.009191   
1       1.0             NaN   0.103009  ...                   -0.123518   
2       2.0             NaN   0.109600  ...                    0.194285   
3       2.0             NaN   0.111599  ...                   -0.073142   
4       1.0             NaN   0.096943  ...                    0.158150   
5       2.0             NaN   0.095377  ...                    0.014290   
6       2.0             NaN   0.092620  ...                   -0.059419   
7       2.0             2.0   0.131462  ...                   -0.283481   
8       1.0             1.0   0.106885  ...                    0.198956   
9       1.0             1.0   0.103268  ...                    0.456875   

   terrorist_0_country  warlord_0_country  d'etat_0_country  \
0            -0.196791          -0.277796         -0.080313   
1            -0.169664          -0.039284          0.096598   
2            -0.051662           0.112230          0.271666   
3            -0.122469           0.135643          0.204327   
4            -0.068429          -0.161717         -0.187331   
5            -0.021839           0.010606         -0.085573   
6            -0.050372          -0.144964         -0.140235   
7            -0.311409          -0.295271         -0.370462   
8             0.232582           0.165008          0.475172   
9            -0.102239           0.338327          0.302879   

   overthrow_0_country  convoys_0_country  carbon_0_country  mayhem_0_country  \
0            -0.158093          -0.091979         -0.205168         -0.351945   
1            -0.145231          -0.058545          0.024883          0.039075   
2             0.351302           0.175470          0.236345          0.159935   
3             0.101177          -0.144836          0.222670          0.156061   
4            -0.139090          -0.142929         -0.010496         -0.081932   
5             0.147253          -0.040194          0.053930         -0.185165   
6            -0.056617          -0.232453         -0.117227          0.117000   
7            -0.298859          -0.246249         -0.109567         -0.168876   
8             0.257077           0.246208          0.089489          0.217305   
9             0.120221           0.354626          0.248271          0.316393   

   dehydrated_0_country  mismanagement_0_country  
0             -0.004046                 0.020729  
1             -0.060053                -0.112890  
2              0.198416                 0.409551  
3              0.274630                 0.180825  
4              0.007388                 0.138598  
5              0.172638                -0.085029  
6             -0.111434                -0.100282  
7             -0.335914                -0.276873  
8              0.162207                 0.096265  
9              0.335178                 0.232545  

[10 rows x 525 columns]

In [77]:
add_agg_factors(t_variant_traditional_factors, level='province')

index      country  admin_code  admin_name year_month  year  month  \
0          30  Afghanistan         202    Kandahar    2009_07  2009      7   
1          33  Afghanistan         202    Kandahar    2009_10  2009     10   
2          36  Afghanistan         202    Kandahar    2010_01  2010      1   
3          39  Afghanistan         202    Kandahar    2010_04  2010      4   
4          42  Afghanistan         202    Kandahar    2010_07  2010      7   
...       ...          ...         ...         ...        ...   ...    ...   
40947  183579     Zimbabwe         612  Zvishavane    2018_10  2018     10   
40948  183583     Zimbabwe         612  Zvishavane    2019_02  2019      2   
40949  183587     Zimbabwe         612  Zvishavane    2019_06  2019      6   
40950  183591     Zimbabwe         612  Zvishavane    2019_10  2019     10   
40951  183595     Zimbabwe         612  Zvishavane    2020_02  2020      2   

       fews_ipc  fews_proj_near  ndvi_mean  ...  mismanagement_0_country  \
0           1.0             NaN   0.106035  ...                 0.020729   
1           1.0             NaN   0.103009  ...                -0.112890   
2           2.0             NaN   0.109600  ...                 0.409551   
3           2.0             NaN   0.111599  ...                 0.180825   
4           1.0             NaN   0.096943  ...                 0.138598   
...         ...             ...        ...  ...                      ...   
40947       3.0             3.0   0.326176  ...                -0.025605   
40948       3.0             3.0   0.497560  ...                 0.007386   
40949       3.0             3.0   0.377050  ...                -0.012794   
40950       3.0             3.0   0.297881  ...                 0.128335   
40951       2.0             2.0   0.539183  ...                      NaN   

       ndvi_mean_province  ndvi_anom_province  rain_mean_province  \
0                0.106035          106.547146            0.353588   
1                0.103009          106.034013            0.409304   
2                0.109600          111.433187            3.894158   
3                0.111599           94.212242            1.609664   
4                0.096943           97.411677            0.393834   
...                   ...                 ...                 ...   
40947            0.327981          100.818479            1.659232   
40948            0.565471           99.732242           25.601771   
40949            0.378612           93.027975            0.440751   
40950            0.293570           90.322740            1.410612   
40951            0.566960          100.146555           31.539219   

       rain_anom_province  et_mean_province  et_anom_province  \
0               -0.070848          0.191125         -0.073903   
1               -0.116134          0.694470          0.225598   
2               -2.333251          3.441319         -1.450951   
3               -0.788739          1.851542         -0.771469   
4               -0.030602          0.291468          0.026441   
...                   ...               ...               ...   
40947           -2.431069          5.150127          1.006574   
40948            4.706243         21.877956          1.191221   
40949           -0.067992          5.389194         -1.045850   
40950           -2.679689          2.653295         -1.490257   
40951           10.523018         23.415726          2.728988   

       acled_count_province  acled_fatalities_province  p_staple_food_province  
0                     0.000                      0.000                1.065669  
1                     0.000                      0.000                1.100531  
2                     0.000                      0.000                0.988390  
3                     0.000                      0.000                0.992492  
4                     0.000                      0.000                1.024889  
...                     ...                        ...        

In [78]:
add_agg_factors(t_variant_traditional_factors, level='country')
add_agg_factors(t_invariant_traditional_factors, level='province')
add_agg_factors(t_invariant_traditional_factors, level='country')

index      country  admin_code  admin_name year_month  year  month  \
0          30  Afghanistan         202    Kandahar    2009_07  2009      7   
1          33  Afghanistan         202    Kandahar    2009_10  2009     10   
2          36  Afghanistan         202    Kandahar    2010_01  2010      1   
3          39  Afghanistan         202    Kandahar    2010_04  2010      4   
4          42  Afghanistan         202    Kandahar    2010_07  2010      7   
...       ...          ...         ...         ...        ...   ...    ...   
40947  183579     Zimbabwe         612  Zvishavane    2018_10  2018     10   
40948  183583     Zimbabwe         612  Zvishavane    2019_02  2019      2   
40949  183587     Zimbabwe         612  Zvishavane    2019_06  2019      6   
40950  183591     Zimbabwe         612  Zvishavane    2019_10  2019     10   
40951  183595     Zimbabwe         612  Zvishavane    2020_02  2020      2   

       fews_ipc  fews_proj_near  ndvi_mean  ...  area_province  \
0           1.0             NaN   0.106035  ...    54174.53381   
1           1.0             NaN   0.103009  ...    54174.53381   
2           2.0             NaN   0.109600  ...    54174.53381   
3           2.0             NaN   0.111599  ...    54174.53381   
4           1.0             NaN   0.096943  ...    54174.53381   
...         ...             ...        ...  ...            ...   
40947       3.0             3.0   0.326176  ...     6198.95825   
40948       3.0             3.0   0.497560  ...     6198.95825   
40949       3.0             3.0   0.377050  ...     6198.95825   
40950       3.0             3.0   0.297881  ...     6198.95825   
40951       2.0             2.0   0.539183  ...     6198.95825   

       cropland_pct_province  pop_province  ruggedness_mean_province  \
0                   1.417796   1241226.000              101047.15870   
1                   1.417796   1241226.000              101047.15870   
2                   1.417796   1280853.000              101047.15870   
3                   1.417796   1280853.000              101047.15870   
4                   1.417796   1280853.000              101047.15870   
...                      ...           ...                       ...   
40947              31.339385    254993.250              113050.19375   
40948              31.339385    260172.625              113050.19375   
40949              31.339385    260172.625              113050.19375   
40950              31.339385    260172.625              113050.19375   
40951              31.339385    265380.150              113050.19375   

       pasture_pct_province  area_country  cropland_pct_country  \
0                 16.246279  18883.616198              7.335028   
1                 16.246279  18883.616198              7.335028   
2                 16.246279  18883.616198              7.335028   
3                 16.246279  18883.616188              7.335028   
4                 16.246279  18883.616188              7.335028   
...                     ...           ...                   ...   
40947             55.568223   6531.261152             31.452557   
40948             55.568223   6531.261152             31.452557   
40949             55.568223   6531.261152             31.452557   
40950             55.568223   6531.261152             31.452557   
40951             55.568223   6531.261152             31.452557   

         pop_country  ruggedness_mean_country  pasture_pct_country  
0      800334.941176            316314.115459            49.145729  
1      800334.941176            316314.115459            49.145729  
2      821226.147059            316314.115459            49.145729  
3      821226.147059            316314.116188            49.145729  
4      821226.147059            316314.116188            49.145729  
...              ...                      ...                  ...  
40947  278500.300000            144621.235150            53.536959  
40948  284723.000000            144621.235150           

In [79]:
time_series.to_csv('agg_province_features.csv')

In [80]:
print(time_series.columns)


Index(['index', 'country', 'admin_code', 'admin_name', 'year_month', 'year',
       'month', 'fews_ipc', 'fews_proj_near', 'ndvi_mean',
       ...
       'area_province', 'cropland_pct_province', 'pop_province',
       'ruggedness_mean_province', 'pasture_pct_province', 'area_country',
       'cropland_pct_country', 'pop_country', 'ruggedness_mean_country',
       'pasture_pct_country'],
      dtype='object', length=553)


# Add time lagged features


In [81]:
time_series = add_time_lagged(t_variant_traditional_factors)

/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: 

In [82]:
time_series = add_time_lagged(news_factors)

/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: 

KeyboardInterrupt: 

In [ ]:
time_series = add_time_lagged(['fews_ipc'], end=21, diff=3, agg=False)

/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: 

In [ ]:
time_series = add_time_lagged(['fews_proj_near'], start=3, end=4, diff=1, agg=False)

/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/871824488.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  time_series[lagged_col] = [get_lagged(row, f_s, t, ts_dict) for _, row in time_series.iterrows()]


In [ ]:
time_series

index      country  admin_code admin_name year_month  year  month  \
0      30  Afghanistan         202   Kandahar    2009_07  2009      7   
1      33  Afghanistan         202   Kandahar    2009_10  2009     10   
2      36  Afghanistan         202   Kandahar    2010_01  2010      1   
3      39  Afghanistan         202   Kandahar    2010_04  2010      4   
4      42  Afghanistan         202   Kandahar    2010_07  2010      7   
5      45  Afghanistan         202   Kandahar    2010_10  2010     10   
6      48  Afghanistan         202   Kandahar    2011_01  2011      1   
7      51  Afghanistan         202   Kandahar    2011_04  2011      4   
8      54  Afghanistan         202   Kandahar    2011_07  2011      7   
9      57  Afghanistan         202   Kandahar    2011_10  2011     10   
10     60  Afghanistan         202   Kandahar    2012_01  2012      1   
11     63  Afghanistan         202   Kandahar    2012_04  2012      4   
12     66  Afghanistan         202   Kandahar    2012_07  2012      7   
13     69  Afghanistan         202   Kandahar    2012_10  2012     10   
14     72  Afghanistan         202   Kandahar    2013_01  2013      1   

    fews_ipc  fews_proj_near  ndvi_mean  ...  mismanagement_0_country_6  \
0        1.0             NaN   0.106035  ...                  -0.073000   
1        1.0             NaN   0.103009  ...                  -0.510467   
2        2.0             NaN   0.109600  ...                   0.530333   
3        2.0             NaN   0.111599  ...                  -1.011600   
4        1.0             NaN   0.096943  ...                  -0.611133   
5        2.0             NaN   0.095377  ...                   0.696667   
6        2.0             NaN   0.092620  ...                   0.357667   
7        2.0             2.0   0.131462  ...                  -0.817600   
8        1.0             1.0   0.106885  ...                   1.217667   
9        1.0             1.0   0.103268  ...                  -0.213000   
10       1.0             1.0   0.094107  ...                   0.993667   
11       1.0             1.0   0.116692  ...                   1.016667   
12       1.0             1.0   0.104068  ...                   0.184000   
13       1.0             1.0   0.101172  ...                  -0.436667   
14       1.0             1.0   0.095679  ...                   0.950000   

    mismanagement_0_country_7  mismanagement_0_country_8  fews_ipc_3  \
0                   -0.073000                  -0.073000         1.0   
1                   -0.510467                  -0.510467         1.0   
2                    0.530333                   0.530333         1.0   
3                   -1.011600                  -1.011600         2.0   
4                   -0.611133                  -0.611133         1.0   
5                    0.696667                   0.696667         2.0   
6                    0.357667                   0.357667         2.0   
7                   -0.817600                  -0.817600         2.0   
8                    1.217667                   1.217667         1.0   
9                   -0.213000                  -0.213000         1.0   
10                   0.993667                   0.993667         1.0   
11                   1.016667                   1.016667         1.0   
12                   0.184000                   0.184000         1.0   
13                  -0.436667                  -0.436667         1.0   
14                   0.950000                   0.950000         1.0   

    fews_ipc_6  fews_ipc_9  fews_ipc_12  fews_ipc_15  fews_ipc_18  \
0          1.0         1.0          1.0          1.0          1.0   
1          1.0         1.0          1.0          1.0          1.0   
2          2.0         2.0          2.0          1.0          2.0   
3          1.0         2.0          2.0          2.0          1.0   
4          1.0         1.0          1.0          1.0          1.0   
5          2.0         2.0          1.0          2.0          2.0  

In [ ]:

time_series.to_csv("time_series1.csv", index=False)

print("Data saved to time_series.csv")

Data saved to time_series.csv


In [ ]:
def find_mismatches(file1, file2):
    """Reads two CSV files and finds exact mismatches by row and column."""
    df1 = pd.read_csv(file1)
    df2 = pd.read_csv(file2)
    
    if df1.shape != df2.shape:
        raise ValueError("The two files have different shapes and cannot be compared directly.")
    
    mismatches = []
    for idx in range(len(df1)):
        for col in df1.columns:
            if col in df2.columns and df1.at[idx, col] != df2.at[idx, col]:
                mismatches.append((idx, col, df1.at[idx, col], df2.at[idx, col]))
    
    return mismatches


def find_column_differences(file1, file2):
    """Finds columns present in one file but absent in the other."""
    df1 = pd.read_csv(file1)
    df2 = pd.read_csv(file2)
    
    cols1 = set(df1.columns)
    cols2 = set(df2.columns)
    
    missing_in_df2 = cols1 - cols2
    missing_in_df1 = cols2 - cols1
    
    return {
        "missing_in_file2": missing_in_df2,
        "missing_in_file1": missing_in_df1
    }



In [ ]:
# find_column_differences('time_series2.csv','time_series1.csv')

In [ ]:
# print(f"The number of mismatch results are {len(find_mismatches('time_series1.csv','time_series2.csv'))}")
# print(f"The total entires{time_series.size}")

In [ ]:
# find_mismatches('time_series1.csv','time_series2.csv')

In [ ]:
def diebold_mariano(preds, labels):
    sq_error = [(p-l)**2 for p,l in zip(preds, labels)]
    mean = np.mean(sq_error)
    n = len(preds)
    gammas = {}
    m = max(n,int(math.ceil(np.cbrt(n))+2))
    for k in range(m):
        gammas[k] = 0
        for i in range(k+1, n):
            gammas[k] += (sq_error[i] - mean)*(sq_error[i-k] - mean)
        gammas[k] = gammas[k]/n
    sum_gamma = gammas[0]
    for k in range(1, m):
        sum_gamma += 2*gammas[k]
    return np.sqrt(sum_gamma/n)

In [ ]:
time_series.columns.shape

(3728,)

In [ ]:
time_series.head()

index      country  admin_code admin_name year_month  year  month  \
0     30  Afghanistan         202   Kandahar    2009_07  2009      7   
1     33  Afghanistan         202   Kandahar    2009_10  2009     10   
2     36  Afghanistan         202   Kandahar    2010_01  2010      1   
3     39  Afghanistan         202   Kandahar    2010_04  2010      4   
4     42  Afghanistan         202   Kandahar    2010_07  2010      7   

   fews_ipc  fews_proj_near  ndvi_mean  ...  mismanagement_0_country_6  \
0       1.0             NaN   0.106035  ...                  -0.073000   
1       1.0             NaN   0.103009  ...                  -0.510467   
2       2.0             NaN   0.109600  ...                   0.530333   
3       2.0             NaN   0.111599  ...                  -1.011600   
4       1.0             NaN   0.096943  ...                  -0.611133   

   mismanagement_0_country_7  mismanagement_0_country_8  fews_ipc_3  \
0                  -0.073000                  -0.073000         1.0   
1                  -0.510467                  -0.510467         1.0   
2                   0.530333                   0.530333         1.0   
3                  -1.011600                  -1.011600         2.0   
4                  -0.611133                  -0.611133         1.0   

   fews_ipc_6  fews_ipc_9  fews_ipc_12  fews_ipc_15  fews_ipc_18  \
0         1.0         1.0          1.0          1.0          1.0   
1         1.0         1.0          1.0          1.0          1.0   
2         2.0         2.0          2.0          1.0          2.0   
3         1.0         2.0          2.0          2.0          1.0   
4         1.0         1.0          1.0          1.0          1.0   

   fews_proj_near_3  
0               NaN  
1               NaN  
2               NaN  
3               NaN  
4               NaN  

[5 rows x 3728 columns]

In [ ]:
# find columns that contain a particular substring

list(filter(lambda x: 'co' in x, time_series.columns))

['country',
 'admin_code',
 'acled_count',
 'continued deterioration_0',
 'economic impoverishment_0',
 'conflict_0',
 'collapsing economy_0',
 'corrupt government_0',
 'continued strife_0',
 'ecological crisis_0',
 'coup_0',
 'economic crisis_0',
 'corruption_0',
 'collapse of government_0',
 'devastated the economy_0',
 'convoys_0',
 'continued deterioration_0_province',
 'economic impoverishment_0_province',
 'conflict_0_province',
 'collapsing economy_0_province',
 'corrupt government_0_province',
 'continued strife_0_province',
 'ecological crisis_0_province',
 'coup_0_province',
 'economic crisis_0_province',
 'corruption_0_province',
 'collapse of government_0_province',
 'devastated the economy_0_province',
 'convoys_0_province',
 'land seizures_0_country',
 'slashed export_0_country',
 'price rise_0_country',
 'mass hunger_0_country',
 'cyclone_0_country',
 'failed crops_0_country',
 'disruption to farming_0_country',
 'massive starvation_0_country',
 'abnormally low rainfall_

In [ ]:
# find columns that begin with a particular substring
list(filter(lambda x: x.startswith("coun"), time_series.columns))


['country']

# Generate and save data


In [ ]:
# import numpy as np
import pandas as pd
from joblib import Parallel, delayed
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression, Lasso
from sklearn.metrics import root_mean_squared_error, precision_recall_curve, auc

train_splits = [((2009,7), (2010,4)), ((2009,7), (2011,1)), ((2009,7), (2011,10)), 
                ((2009,7), (2012,7)), ((2009,7), (2013,7)), ((2009,7), (2014,1)), 
                ((2009,7), (2015,1)), ((2009,7), (2015,10)), ((2009,7), (2016,10)), 
                ((2009,7), (2017,2))]

dev_splits = [((2010,4), (2010, 7)), ((2011,1), (2011, 7)), ((2011,10), (2012, 7)), 
              ((2012,7), (2013, 7)), ((2013,4), (2014, 7)), ((2014,1), (2015, 7)), 
              ((2015,1), (2016, 7)), ((2015,10), (2017, 7)), ((2016,10), (2018, 7)), 
              ((2017,2), (2019, 2))]

test_splits = [((2010,7), (2011, 7)), ((2011,7), (2012, 7)), ((2012,7), (2013, 7)), 
               ((2013,7), (2014, 7)), ((2014,7), (2015, 7)), ((2015,7), (2016, 7)), 
               ((2016,7), (2017, 7)), ((2017,7), (2018, 7)), ((2018,7), (2019, 7)), 
               ((2019,2), (2020, 2))]

# just like them we will evaluate three dufferent models, Random Forest, OLS and Lasso. Random Forest is a tree-based model, OLS is a linear regression model and Lasso is a linear regression model with L1 regularization
models = {
    'RF': RandomForestRegressor(max_features='sqrt', n_estimators=100, min_samples_split=0.5, min_impurity_decrease=0.001, random_state=0),
    'OLS': LinearRegression(),
    'Lasso': Lasso(alpha=0.1)
}

def get_agg_lagged_features(factors):
    return [f"{f}_{t}" for f in factors for t in range(3, 9)] + \
           [f"{f}_province_{t}" for f in factors for t in range(3, 9)] + \
           [f"{f}_country_{t}" for f in factors for t in range(3, 9)]

features = {
    'traditional': time_series[['year', 'month'] + 
        [f"fews_ipc_{t}" for t in range(3, 21, 3)] + 
        get_agg_lagged_features(t_variant_traditional_factors) + 
        t_invariant_traditional_factors],
    
    'news': time_series[['year', 'month'] + 
        [f"fews_ipc_{t}" for t in range(3, 21, 3)] + 
        get_agg_lagged_features(news_factors)],
    
    'traditional+news': time_series[['year', 'month'] + 
        [f"fews_ipc_{t}" for t in range(3, 21, 3)] + 
        get_agg_lagged_features(t_variant_traditional_factors) + 
        t_invariant_traditional_factors + 
        get_agg_lagged_features(news_factors)]
}

labels_df = time_series[['fews_ipc', 'year', 'month']]

def get_time_split(df, start, end):
    return df[
        (((df['year'] > start[0])) | ((df['year'] == start[0]) & (df['month'] >= start[1]))) &
        (((df['year'] < end[0])) | ((df['year'] == end[0]) & (df['month'] <= end[1])))
    ]

thresholds = {
    'traditional': (2.236, 3.125), 'news': (1.907, 2.712), 'traditional+news': (2.105, 3.314),
} # (lowerbound, upperbound)

def train_and_evaluate(train, dev, test, f, D):
    results = []

    X_train = get_time_split(D, train[0], dev[1]).drop(columns=['year', 'month']).fillna(0).to_numpy() # not sure how okay it is to do fillna. When me and Bilal were running this we were getting the error that cannot run the model on NaN values. First we dropped na but this was causing the shape of the X_train to be different from the y_train. So we decided to fillna with 0. - aysha & bilal
    y_train = get_time_split(labels_df, train[0], dev[1]).drop(columns=['year', 'month']).to_numpy().ravel()
    
    X_test = get_time_split(D, test[0], test[1]).drop(columns=['year', 'month']).fillna(0).to_numpy()
    y_test = get_time_split(labels_df, test[0], test[1]).drop(columns=['year', 'month']).to_numpy().ravel()
    
    # convert y_test into binary classification (1 if inside threshold, else 0)
    lower, upper = thresholds[f]
    y_test_binary = np.where((y_test >= lower) & (y_test <= upper), 1, 0)

    for name, model in models.items():
        model.fit(X_train, y_train)
        preds = model.predict(X_test)

        rmse = root_mean_squared_error(y_test, preds)

        stderr = np.std(y_test - preds) / np.sqrt(len(y_test))
        upper_bound = np.sqrt(rmse**2 + 1.96 * stderr)
        lower_bound = np.sqrt(rmse**2 - 1.96 * stderr)

        precision, recall, _ = precision_recall_curve(y_test_binary, preds)
        aucpr = auc(recall, precision)

        results.append({
            'method': name, 'split': test, 'features': f, 
            'rmse': rmse, 'lower_bound': lower_bound, 'upper_bound': upper_bound,
            'aucpr': aucpr
        })

        print(f"Method: {name}, Split: {test}, Features: {f}, AUCPR: {aucpr:.4f}")
        print(f"Method: {name}, Split: {test}, Features: {f}, RMSE: {rmse:.4f} [{lower_bound:.4f}, {upper_bound:.4f}]")
        
        # completely removed the part where they were doing country-wise evaluation. Do not see point - aysha
    
    return results

# run in parallel on 4 cpu cores/decrease this if you do not want ur system to crash (speaking from experience)
all_results = Parallel(n_jobs=4)(
    delayed(train_and_evaluate)(train, dev, test, f, D) for train, dev, test in zip(train_splits, dev_splits, test_splits) for f, D in features.items()
)

fig_3a = pd.DataFrame([res for sublist in all_results for res in sublist])
fig_3a.to_csv('fig_3a.csv', index=False)


/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warn

Method: RF, Split: ((2010, 7), (2011, 7)), Features: traditional, AUCPR: 0.5000
Method: RF, Split: ((2010, 7), (2011, 7)), Features: traditional, RMSE: 0.5078 [nan, 0.7759]
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: traditional, AUCPR: 0.5000
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: traditional, RMSE: 0.6672 [nan, 0.9482]
Method: Lasso, Split: ((2010, 7), (2011, 7)), Features: traditional, AUCPR: 0.5000
Method: Lasso, Split: ((2010, 7), (2011, 7)), Features: traditional, RMSE: 0.8343 [nan, 1.1945]
Method: RF, Split: ((2011, 7), (2012, 7)), Features: traditional, AUCPR: 0.5000
Method: RF, Split: ((2011, 7), (2012, 7)), Features: traditional, RMSE: 0.5982 [0.2073, 0.8202]
Method: OLS, Split: ((2011, 7), (2012, 7)), Features: traditional, AUCPR: 0.5000
Method: OLS, Split: ((2011, 7), (2012, 7)), Features: traditional, RMSE: 0.5637 [nan, 0.8689]
Method: Lasso, Split: ((2011, 7), (2012, 7)), Features: traditional, AUCPR: 0.5000
Method: Lasso, Split: ((2011, 7), (2012

/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(


Method: RF, Split: ((2010, 7), (2011, 7)), Features: news, AUCPR: 0.9028
Method: RF, Split: ((2010, 7), (2011, 7)), Features: news, RMSE: 0.4091 [nan, 0.7131]
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: news, AUCPR: 0.7639
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: news, RMSE: 0.4581 [nan, 0.7787]
Method: Lasso, Split: ((2010, 7), (2011, 7)), Features: news, AUCPR: 0.9028
Method: Lasso, Split: ((2010, 7), (2011, 7)), Features: news, RMSE: 0.5171 [nan, 0.8353]
Method: RF, Split: ((2010, 7), (2011, 7)), Features: traditional+news, AUCPR: 0.5000
Method: RF, Split: ((2010, 7), (2011, 7)), Features: traditional+news, RMSE: 0.4294 [nan, 0.7285]
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: traditional+news, AUCPR: 0.5000
Method: OLS, Split: ((2010, 7), (2011, 7)), Features: traditional+news, RMSE: 0.4642 [nan, 0.7844]


/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encounter

...

/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(


Method: RF, Split: ((2011, 7), (2012, 7)), Features: traditional+news, AUCPR: 0.5000
Method: RF, Split: ((2011, 7), (2012, 7)), Features: traditional+news, RMSE: 0.5878 [0.4409, 0.7047]
Method: OLS, Split: ((2011, 7), (2012, 7)), Features: traditional+news, AUCPR: 0.5000
Method: OLS, Split: ((2011, 7), (2012, 7)), Features: traditional+news, RMSE: 0.9621 [0.7256, 1.1509]
Method: Lasso, Split: ((2011, 7), (2012, 7)), Features: traditional+news, AUCPR: 0.5000
Method: Lasso, Split: ((2011, 7), (2012, 7)), Features: traditional+news, RMSE: 0.8912 [0.6111, 1.1023]


/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encountered in sqrt
/Users/wajihanaveed/Library/Python/3.9/lib/python/site-packages/sklearn/metrics/_ranking.py:1033: UserWarning: No positive class found in y_true, recall is set to one for all thresholds.
  warnings.warn(
/var/folders/2b/1yzz7bcn205dx3sqkbz883x00000gn/T/ipykernel_14575/1801067917.py:85: RuntimeWarning: invalid value encounter

Method: RF, Split: ((2012, 7), (2013, 7)), Features: news, AUCPR: 0.5000
Method: RF, Split: ((2012, 7), (2013, 7)), Features: news, RMSE: 0.3876 [0.2015, 0.5098]
Method: OLS, Split: ((2012, 7), (2013, 7)), Features: news, AUCPR: 0.5000
Method: OLS, Split: ((2012, 7), (2013, 7)), Features: news, RMSE: 0.3448 [nan, 0.5946]
Method: Lasso, Split: ((2012, 7), (2013, 7)), Features: news, AUCPR: 0.5000
Method: Lasso, Split: ((2012, 7), (2013, 7)), Features: news, RMSE: 0.2283 [nan, 0.3744]
Method: RF, Split: ((2012, 7), (2013, 7)), Features: traditional+news, AUCPR: 0.5000
Method: RF, Split: ((2012, 7), (2013, 7)), Features: traditional+news, RMSE: 0.3308 [nan, 0.4776]
Method: OLS, Split: ((2012, 7), (2013, 7)), Features: traditional+news, AUCPR: 0.5000
Method: OLS, Split: ((2012, 7), (2013, 7)), Features: traditional+news, RMSE: 0.2670 [nan, 0.4958]
Method: Lasso, Split: ((2012, 7), (2013, 7)), Features: traditional+news, AUCPR: 0.5000
Method: Lasso, Split: ((2012, 7), (2013, 7)), Features: 

ValueError: Found array with 0 sample(s) (shape=(0, 173)) while a minimum of 1 is required by RandomForestRegressor.

In [ ]:
# def safe_train_and_evaluate(train, dev, test, f, D):
#     """Train and evaluate models safely, skipping empty datasets."""
    
#     X_train = get_time_split(D, train[0], dev[1]).drop(columns=['year', 'month']).fillna(0).to_numpy()
#     y_train = get_time_split(labels_df, train[0], dev[1]).drop(columns=['year', 'month']).to_numpy().ravel()

#     X_test = get_time_split(D, test[0], test[1]).drop(columns=['year', 'month']).fillna(0).to_numpy()
#     y_test = get_time_split(labels_df, test[0], test[1]).drop(columns=['year', 'month']).to_numpy().ravel()

#     # 🚨 Check if datasets are empty before proceeding
#     if X_train.shape[0] == 0 or X_test.shape[0] == 0:
#         print(f"⚠️ Skipping empty dataset (train: {X_train.shape}, test: {X_test.shape}) for {f} in split {test}")
#         return [{'method': None, 'split': test, 'features': f, 'rmse': None, 'aucpr': None, 'status': 'Empty dataset'}]

#     lower, upper = thresholds[f]
#     y_test_binary = np.where((y_test >= lower) & (y_test <= upper), 1, 0)

#     results = []
#     for name, model in models.items():
#         model.fit(X_train, y_train)
#         preds = model.predict(X_test)

#         rmse = np.sqrt(np.mean((y_test - preds) ** 2))

#         stderr = np.std(y_test - preds) / np.sqrt(len(y_test))
#         upper_bound = np.sqrt(rmse**2 + 1.96 * stderr)
#         lower_bound = np.sqrt(rmse**2 - 1.96 * stderr)

#         precision, recall, _ = precision_recall_curve(y_test_binary, preds)
#         aucpr = auc(recall, precision)

#         results.append({
#             'method': name, 'split': test, 'features': f,
#             'rmse': rmse, 'lower_bound': lower_bound, 'upper_bound': upper_bound,
#             'aucpr': aucpr, 'status': 'Success'
#         })

#         print(f"[{name}] Split: {test}, Features: {f}, AUCPR: {aucpr:.4f}")
#         print(f"[{name}] Split: {test}, RMSE: {rmse:.4f} [{lower_bound:.4f}, {upper_bound:.4f}]")

#     return results
# # Run Parallel Execution Safely
# all_results = Parallel(n_jobs=4)(
#     delayed(safe_train_and_evaluate)(train, dev, test, f, D)
#     for train, dev, test in zip(train_splits, dev_splits, test_splits)
#     for f, D in features.items()
# )

